# Single Pair

# Import python libraries

In [1]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import statsmodels
from statsmodels.tsa.stattools import coint

import yfinance as yf

import time

import datetime
from datetime import datetime
from datetime import timedelta

import statistics
import scipy.stats as st
from scipy.stats import norm
import math

# SELECT PAIR

In [2]:
try:
    print(ticker_list)
except:
    
    ticker_list = [ 
                    ['RIO', 'USD'], #If doing cross market, put the US stock first
                ['RIO.AX', 'AUD'],
              ]      

# Download Prices from Yahoo

In [3]:
i = 0
for ticker in ticker_list:
  print('Ticker = ', ticker[0])
  print('i = ', i)
  data = yf.download(ticker[0], start="1972-01-01", end="2030-01-01")
  data['Ticker'] = ticker[0]
  data['Currency'] = ticker[1]
  data.reset_index(inplace=True)
  if i == 0:
    stock_prices_df = data
  if i> 0:
    stock_prices_df = pd.concat([stock_prices_df, data])

  time.sleep(0.25)    # pause 0.25 seconds
  
  i = i+1

stock_prices_df.rename(columns={'Close': 'Stock Close','Adj Close': 'Stock Adj Close'}, inplace=True)

stock_prices_df

Ticker =  RIO
i =  0
[*********************100%***********************]  1 of 1 completed
Ticker =  RIO.AX
i =  1
[*********************100%***********************]  1 of 1 completed


Date        Open        High         Low  Stock Close  \
0    1990-06-28   10.093750   10.093750    9.968750     9.968750   
1    1990-06-29   10.031250   10.062500   10.000000    10.062500   
2    1990-07-02   10.000000   10.031250   10.000000    10.031250   
3    1990-07-03   10.031250   10.062500   10.031250    10.062500   
4    1990-07-05    9.718750    9.718750    9.656250     9.687500   
...         ...         ...         ...         ...          ...   
6124 2023-03-10  119.400002  119.949997  116.680000   117.279999   
6125 2023-03-13  117.870003  119.360001  117.330002   118.459999   
6126 2023-03-14  118.459999  118.459999  116.540001   117.519997   
6127 2023-03-15  118.989998  120.080002  118.440002   119.550003   
6128 2023-03-17  114.099998  115.839996  114.099998   115.779999   

      Stock Adj Close   Volume  Ticker Currency  
0            2.052645   176400     RIO      USD  
1            2.071948    69200     RIO      USD  
2            2.065514    62000     RIO      USD  
3            2.071948    29600     RIO      USD  
4            1.994733    31200     RIO      USD  
...               ...      ...     ...      ...  
6124       117.279999  1584400  RIO.AX      AUD  
6125       118.459999  1013311  RIO.AX      AUD  
6126       117.519997  1459404  RIO.AX      AUD  
6127       119.550003  1530996  RIO.AX      AUD  
6128       115.779999  1554487  RIO.AX      AUD  

[14351 rows x 9 columns]

In [4]:
stock_prices_df['Ticker'].unique()

array(['RIO', 'RIO.AX'], dtype=object)

# Add FX Rates

In [5]:
def download_fx_rates():
  sgd_df = yf.download('SGD=X', start="1972-01-01", end="2030-01-01")
  sgd_df.reset_index(inplace=True)
  sgd_df.rename(columns={'Close': 'SGD'}, inplace=True)
  sgd_df = sgd_df[['Date','SGD']].copy()

  aud_df = yf.download('AUDUSD=X', start="1972-01-01", end="2030-01-01")
  aud_df.reset_index(inplace=True)
  aud_df.rename(columns={'Close': 'AUD'}, inplace=True)
  aud_df = aud_df[['Date','AUD']].copy()

  jpy_df = yf.download('USDJPY=X', start="1972-01-01", end="2030-01-01")
  jpy_df.reset_index(inplace=True)
  jpy_df.rename(columns={'Close': 'JPY'}, inplace=True)
  jpy_df = jpy_df[['Date','JPY']].copy()

  eur_df = yf.download('EUR=X', start="1972-01-01", end="2030-01-01")
  eur_df.reset_index(inplace=True)
  eur_df.rename(columns={'Close': 'EUR'}, inplace=True)
  eur_df = eur_df[['Date','EUR']].copy()

  return sgd_df, aud_df, jpy_df, eur_df

In [6]:
def merge_fx_rates(stock_prices_df, sgd_df, aud_df, jpy_df, eur_df):
  stock_df = stock_prices_df.copy()

  stock_df = pd.merge(stock_df, sgd_df, how='outer', left_on='Date', right_on="Date")
  stock_df = pd.merge(stock_df, aud_df, how='outer', left_on='Date', right_on="Date")
  stock_df['AUD'] = 1 / stock_df['AUD'] #Invert AUD rate so we can treat it consisently with other currencies
  stock_df = pd.merge(stock_df, jpy_df, how='outer', left_on='Date', right_on="Date")
  stock_df = pd.merge(stock_df, eur_df, how='outer', left_on='Date', right_on="Date")
  stock_df['EUR'] = 1 / stock_df['EUR'] #Invert EUR rate so we can treat it consisently with other currencies
  stock_df['USD'] = 1
  stock_df['HKD'] = 7.75

  stock_df.dropna(subset=['Ticker'], inplace=True)
  stock_df.sort_values('Date', inplace=True)

  stock_df['Stock USD Close'] = stock_df['Stock Close']
  stock_df['Stock USD Adj Close'] = stock_df['Stock Adj Close']
  stock_df['Stock USD Open'] = stock_df['Open']

  ccy_list = stock_df['Currency'].unique().tolist()

  for ccy in ccy_list:

    stock_df.loc[stock_df['Currency'] == ccy, 'Stock USD Close'] = \
          stock_df['Stock USD Close'] / stock_df[ccy]

    stock_df.loc[stock_df['Currency'] == ccy, 'Stock USD Adj Close'] = \
          stock_df['Stock USD Adj Close'] / stock_df[ccy]
    
    stock_df.loc[stock_df['Currency'] == ccy, 'Stock USD Open'] = \
      stock_df['Stock USD Open'] / stock_df[ccy]


  return stock_df, ccy_list


In [7]:
# Stock Prices DF Before Adding FX rates
stock_prices_df

Date        Open        High         Low  Stock Close  \
0    1990-06-28   10.093750   10.093750    9.968750     9.968750   
1    1990-06-29   10.031250   10.062500   10.000000    10.062500   
2    1990-07-02   10.000000   10.031250   10.000000    10.031250   
3    1990-07-03   10.031250   10.062500   10.031250    10.062500   
4    1990-07-05    9.718750    9.718750    9.656250     9.687500   
...         ...         ...         ...         ...          ...   
6124 2023-03-10  119.400002  119.949997  116.680000   117.279999   
6125 2023-03-13  117.870003  119.360001  117.330002   118.459999   
6126 2023-03-14  118.459999  118.459999  116.540001   117.519997   
6127 2023-03-15  118.989998  120.080002  118.440002   119.550003   
6128 2023-03-17  114.099998  115.839996  114.099998   115.779999   

      Stock Adj Close   Volume  Ticker Currency  
0            2.052645   176400     RIO      USD  
1            2.071948    69200     RIO      USD  
2            2.065514    62000     RIO      USD  
3            2.071948    29600     RIO      USD  
4            1.994733    31200     RIO      USD  
...               ...      ...     ...      ...  
6124       117.279999  1584400  RIO.AX      AUD  
6125       118.459999  1013311  RIO.AX      AUD  
6126       117.519997  1459404  RIO.AX      AUD  
6127       119.550003  1530996  RIO.AX      AUD  
6128       115.779999  1554487  RIO.AX      AUD  

[14351 rows x 9 columns]

In [8]:
#Run functions to download and merge FX Rates

sgd_df, aud_df, jpy_df, eur_df = download_fx_rates()
stock_prices_df, ccy_list = merge_fx_rates(stock_prices_df, sgd_df, aud_df, jpy_df, eur_df)

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


In [9]:
aud_df

Date       AUD
0    2006-05-16  0.767106
1    2006-05-17  0.759417
2    2006-05-18  0.764000
3    2006-05-19  0.757174
4    2006-05-22  0.753409
...         ...       ...
4377 2023-03-13  0.663420
4378 2023-03-14  0.665920
4379 2023-03-15  0.668910
4380 2023-03-16  0.661830
4381 2023-03-17  0.668847

[4382 rows x 2 columns]

In [10]:
stock_prices_df

Date        Open        High         Low  Stock Close  \
0     1990-06-28   10.093750   10.093750    9.968750     9.968750   
1     1990-06-29   10.031250   10.062500   10.000000    10.062500   
2     1990-07-02   10.000000   10.031250   10.000000    10.031250   
3     1990-07-03   10.031250   10.062500   10.031250    10.062500   
4     1990-07-05    9.718750    9.718750    9.656250     9.687500   
...          ...         ...         ...         ...          ...   
14184 2023-03-14  118.459999  118.459999  116.540001   117.519997   
14186 2023-03-15  118.989998  120.080002  118.440002   119.550003   
14185 2023-03-15   66.620003   67.150002   64.610001    65.870003   
14187 2023-03-16   64.190002   65.300003   64.110001    64.730003   
14350 2023-03-17  114.099998  115.839996  114.099998   115.779999   

       Stock Adj Close     Volume  Ticker Currency      SGD       AUD  \
0             2.052645   176400.0     RIO      USD      NaN       NaN   
1             2.071948    69200.0     RIO      USD      NaN       NaN   
2             2.065514    62000.0     RIO      USD      NaN       NaN   
3             2.071948    29600.0     RIO      USD      NaN       NaN   
4             1.994733    31200.0     RIO      USD      NaN       NaN   
...                ...        ...     ...      ...      ...       ...   
14184       117.519997  1459404.0  RIO.AX      AUD  1.34680  1.501682   
14186       119.550003  1530996.0  RIO.AX      AUD  1.34508  1.494970   
14185        65.870003  6475300.0     RIO      USD  1.34508  1.494970   
14187        64.730003  9800490.0     RIO      USD  1.35101  1.510962   
14350       115.779999  1554487.0  RIO.AX      AUD  1.34468  1.495110   

              JPY       EUR  USD   HKD  Stock USD Close  Stock USD Adj Close  \
0             NaN       NaN    1  7.75         9.968750             2.052645   
1             NaN       NaN    1  7.75        10.062500             2.071948   
2             NaN       NaN    1  7.75        10.031250             2.065514   
3             NaN       NaN    1  7.75        10.062500             2.071948   
4             NaN       NaN    1  7.75         9.687500             1.994733   
...           ...       ...  ...   ...              ...                  ...   
14184  133.113998  1.072501    1  7.75        78.258904            78.258904   
14186  134.397003  1.072766    1  7.75        79.968167            79.968167   
14185  134.397003  1.072766    1  7.75        65.870003            65.870003   
14187  132.929001  1.058335    1  7.75        64.730003            64.730003   
14350  133.266006  1.063490    1  7.75        77.439115            77.439115   

       Stock USD Open  
0           10.093750  
1           10.031250  
2           10.000000  
3           10.031250  
4            9.718750  
...               ...  
14184       78.884871  
14186       79.593574  
14185       66.620003  
14187       64.190002  
14350       76.315451  

[14351 rows x 18 columns]

# Format Data Files

## Convert to Datetime

In [11]:
#Convert date to datetime : Stocks File
stock_prices_df['Date'] = pd.to_datetime(stock_prices_df['Date'], format='%Y-%m-%d')
stock_prices_df.sort_values(['Ticker', 'Date'], inplace=True)

## Delete Un-necessary columns

In [12]:
stock_prices_df


Date        Open        High         Low  Stock Close  \
0     1990-06-28   10.093750   10.093750    9.968750     9.968750   
1     1990-06-29   10.031250   10.062500   10.000000    10.062500   
2     1990-07-02   10.000000   10.031250   10.000000    10.031250   
3     1990-07-03   10.031250   10.062500   10.031250    10.062500   
4     1990-07-05    9.718750    9.718750    9.656250     9.687500   
...          ...         ...         ...         ...          ...   
14180 2023-03-10  119.400002  119.949997  116.680000   117.279999   
14182 2023-03-13  117.870003  119.360001  117.330002   118.459999   
14184 2023-03-14  118.459999  118.459999  116.540001   117.519997   
14186 2023-03-15  118.989998  120.080002  118.440002   119.550003   
14350 2023-03-17  114.099998  115.839996  114.099998   115.779999   

       Stock Adj Close     Volume  Ticker Currency      SGD       AUD  \
0             2.052645   176400.0     RIO      USD      NaN       NaN   
1             2.071948    69200.0     RIO      USD      NaN       NaN   
2             2.065514    62000.0     RIO      USD      NaN       NaN   
3             2.071948    29600.0     RIO      USD      NaN       NaN   
4             1.994733    31200.0     RIO      USD      NaN       NaN   
...                ...        ...     ...      ...      ...       ...   
14180       117.279999  1584400.0  RIO.AX      AUD  1.35322  1.517220   
14182       118.459999  1013311.0  RIO.AX      AUD  1.34738  1.507340   
14184       117.519997  1459404.0  RIO.AX      AUD  1.34680  1.501682   
14186       119.550003  1530996.0  RIO.AX      AUD  1.34508  1.494970   
14350       115.779999  1554487.0  RIO.AX      AUD  1.34468  1.495110   

              JPY       EUR  USD   HKD  Stock USD Close  Stock USD Adj Close  \
0             NaN       NaN    1  7.75         9.968750             2.052645   
1             NaN       NaN    1  7.75        10.062500             2.071948   
2             NaN       NaN    1  7.75        10.031250             2.065514   
3             NaN       NaN    1  7.75        10.062500             2.071948   
4             NaN       NaN    1  7.75         9.687500             1.994733   
...           ...       ...  ...   ...              ...                  ...   
14180  136.395004  1.058470    1  7.75        77.299268            77.299268   
14182  134.979996  1.068365    1  7.75        78.588778            78.588778   
14184  133.113998  1.072501    1  7.75        78.258904            78.258904   
14186  134.397003  1.072766    1  7.75        79.968167            79.968167   
14350  133.266006  1.063490    1  7.75        77.439115            77.439115   

       Stock USD Open  
0           10.093750  
1           10.031250  
2           10.000000  
3           10.031250  
4            9.718750  
...               ...  
14180       78.696562  
14182       78.197362  
14184       78.884871  
14186       79.593574  
14350       76.315451  

[14351 rows x 18 columns]

In [13]:
stock_prices_df.drop(columns=['High', 'Low', 
                              #'Stock Close',
                              #'Open',
                              'Volume'], inplace=True)


In [14]:
stock_prices_df.tail()

Date        Open  Stock Close  Stock Adj Close  Ticker Currency  \
14180 2023-03-10  119.400002   117.279999       117.279999  RIO.AX      AUD   
14182 2023-03-13  117.870003   118.459999       118.459999  RIO.AX      AUD   
14184 2023-03-14  118.459999   117.519997       117.519997  RIO.AX      AUD   
14186 2023-03-15  118.989998   119.550003       119.550003  RIO.AX      AUD   
14350 2023-03-17  114.099998   115.779999       115.779999  RIO.AX      AUD   

           SGD       AUD         JPY       EUR  USD   HKD  Stock USD Close  \
14180  1.35322  1.517220  136.395004  1.058470    1  7.75        77.299268   
14182  1.34738  1.507340  134.979996  1.068365    1  7.75        78.588778   
14184  1.34680  1.501682  133.113998  1.072501    1  7.75        78.258904   
14186  1.34508  1.494970  134.397003  1.072766    1  7.75        79.968167   
14350  1.34468  1.495110  133.266006  1.063490    1  7.75        77.439115   

       Stock USD Adj Close  Stock USD Open  
14180            77.299268       78.696562  
14182            78.588778       78.197362  
14184            78.258904       78.884871  
14186            79.968167       79.593574  
14350            77.439115       76.315451

# CoIntegration Between Individual Stocks

### Limit Date Range

In [15]:
start_date = '1960-01-01'
end_date = '2030-12-31'


In [16]:
ticker_df = stock_prices_df.copy()
ticker_df = ticker_df[ticker_df['Date'] > start_date].copy()
ticker_df = ticker_df[ticker_df['Date'] < end_date].copy()

In [17]:
ticker_df.set_index('Date', inplace=True)

## Set Historical Vol Period and Stop Loss Limit

In [18]:
vol_period = 20
loss_limit = 10

## Add Daily Returns

In [19]:
#Add daily returns & drop Closing Price Column

#Stocks
ticker_df['Stock Daily Return'] = \
ticker_df.groupby('Ticker')['Stock USD Adj Close'].pct_change()*100

In [20]:
ticker_df = ticker_df[ticker_df['Stock Daily Return'] < 50]
ticker_df = ticker_df[ticker_df['Stock Daily Return'] > -50]
ticker_df

Open  Stock Close  Stock Adj Close  Ticker Currency  \
Date                                                                    
1990-06-29   10.031250    10.062500         2.071948     RIO      USD   
1990-07-02   10.000000    10.031250         2.065514     RIO      USD   
1990-07-03   10.031250    10.062500         2.071948     RIO      USD   
1990-07-05    9.718750     9.687500         1.994733     RIO      USD   
1990-07-06    9.750000     9.750000         2.007603     RIO      USD   
...                ...          ...              ...     ...      ...   
2023-03-10  119.400002   117.279999       117.279999  RIO.AX      AUD   
2023-03-13  117.870003   118.459999       118.459999  RIO.AX      AUD   
2023-03-14  118.459999   117.519997       117.519997  RIO.AX      AUD   
2023-03-15  118.989998   119.550003       119.550003  RIO.AX      AUD   
2023-03-17  114.099998   115.779999       115.779999  RIO.AX      AUD   

                SGD       AUD         JPY       EUR  USD   HKD  \
Date                                                             
1990-06-29      NaN       NaN         NaN       NaN    1  7.75   
1990-07-02      NaN       NaN         NaN       NaN    1  7.75   
1990-07-03      NaN       NaN         NaN       NaN    1  7.75   
1990-07-05      NaN       NaN         NaN       NaN    1  7.75   
1990-07-06      NaN       NaN         NaN       NaN    1  7.75   
...             ...       ...         ...       ...  ...   ...   
2023-03-10  1.35322  1.517220  136.395004  1.058470    1  7.75   
2023-03-13  1.34738  1.507340  134.979996  1.068365    1  7.75   
2023-03-14  1.34680  1.501682  133.113998  1.072501    1  7.75   
2023-03-15  1.34508  1.494970  134.397003  1.072766    1  7.75   
2023-03-17  1.34468  1.495110  133.266006  1.063490    1  7.75   

            Stock USD Close  Stock USD Adj Close  Stock USD Open  \
Date                                                               
1990-06-29        10.062500             2.071948       10.031250   
1990-07-02        10.031250             2.065514       10.000000   
1990-07-03        10.062500             2.071948       10.031250   
1990-07-05         9.687500             1.994733        9.718750   
1990-07-06         9.750000             2.007603        9.750000   
...                     ...                  ...             ...   
2023-03-10        77.299268            77.299268       78.696562   
2023-03-13        78.588778            78.588778       78.197362   
2023-03-14        78.258904            78.258904       78.884871   
2023-03-15        79.968167            79.968167       79.593574   
2023-03-17        77.439115            77.439115       76.315451   

            Stock Daily Return  
Date                            
1990-06-29            0.940412  
1990-07-02           -0.310562  
1990-07-03            0.311529  
1990-07-05           -3.726712  
1990-07-06            0.645209  
...                        ...  
2023-03-10           -3.302268  
2023-03-13            1.668204  
2023-03-14           -0.419746  
2023-03-15            2.184113  
2023-03-17           -3.162574  

[12478 rows x 15 columns]

## Create Price Series

In [21]:
### Creating Price Series1 and Price Series2 
def create_series(ticker1, ticker2, ticker_df, cross_market_settings):

    if cross_market_settings == True:
        
        series1 = ticker_df.loc[ticker_df['Ticker'] == ticker1, 'Stock USD Open']
    else:
        
        series1 = ticker_df.loc[ticker_df['Ticker'] == ticker1, 'Stock USD Close']
        
    series2 = ticker_df.loc[ticker_df['Ticker'] == ticker2, 'Stock USD Close']

    #This section is to ensure the two series are the same length
    sample1_df = pd.DataFrame(data=series1)
    sample1_df.rename(columns={'Stock USD Close': ticker1}, inplace=True)

    sample2_df = pd.DataFrame(data=series2)
    sample2_df.rename(columns={'Stock USD Close': ticker2}, inplace=True)

    #sample_df['Ticker2'] = series2
    #sample_df.rename(columns={'Ticker2': ticker2}, inplace=True)

    sample_df = pd.merge(sample1_df, sample2_df, left_index=True, right_index=True)

    sample_df = sample_df.dropna()
    series1 = sample_df.iloc[:,0]
    series2 = sample_df.iloc[:,1]
    ##

    return series1, series2


## Calculate Number of Crosses

In [22]:
#Calculate number of times ratio passes through median ratio value

def median_cross_count(series1,series2, series_median):
  series_df = pd.DataFrame(data=series1/series2, columns=['Ratio'])

  #If no median value is "force fed", use the median for the current series
  # We force feed the median from the train set into the test set
  if series_median == 0:
    series_median = np.median(series1/series2)
  series_df['Above Below'] = 'B'
  series_df.loc[series_df['Ratio'] > series_median, 'Above Below'] = "A"

  series_df['Prior Above Below'] = 'B'
  # Need to make the first row NA given no prior to reference
  series_df.loc[series_df.index[0], 'Prior Above Below'] = "NA"
  series_df.loc[series_df['Ratio'].shift(1) > series_median, 'Prior Above Below'] = "A"

  series_df['Counter'] = 0
  series_df.loc[series_df[ 'Above Below'] != series_df['Prior Above Below'], 'Counter'] = 1
  # Need to make the first row NA given no prior to reference
  series_df.loc[series_df.index[0], 'Counter'] = 0

  #Make Data A Column Instead of the Index
  series_df.reset_index(inplace=True)

  median_count = series_df['Counter'].sum()
  #print('The number of times passing through Median Value: ', median_count)

  #When was the last median cross

  last_cross = series_df.groupby('Counter').last()
  first_cross = series_df.groupby('Counter').first()
  last_date = series_df.loc[series_df.index[-1],'Date']

  if median_count != 0:
    last_cross = last_cross.loc[1,'Date']
    first_cross = first_cross.loc[1,'Date']

    last_cross = pd.to_datetime(last_cross, format='%Y-%m-%d')
    first_cross = pd.to_datetime(first_cross, format='%Y-%m-%d')
    last_date = pd.to_datetime(last_date, format='%Y-%m-%d')

    days_last_cross = (last_date - last_cross).days

  else:
    days_last_cross = 10000
    last_cross = pd.to_datetime('2000-01-01', format='%Y-%m-%d')
    first_cross = pd.to_datetime('1990-01-01', format='%Y-%m-%d')

  #print('Train Set Series Median: ', series_median)

  return series_df, median_count, first_cross, last_cross, series_median, days_last_cross

## Function for Calculating Regularity of Crossing

In [23]:
def regularity_of_crossing_func(series1, series2, series_median):
    
    ratio = series1 / series2
    total_records = len(ratio)
   
    #Split the term into periods
    num_periods = 6    
    mini_records = int(total_records/ num_periods)
    
    period_cross_count = 0
    
    for i in range(num_periods):
       
        mini_ratio = ratio[i*mini_records:(i+1)*mini_records]
        
        # If initial value is below median but max is above median, cross has occurred
        if mini_ratio[0] < series_median:
            if mini_ratio.max() >= series_median:
                mini_cross = 1
            else:
                mini_cross = 0
        # If initial value is above median but min is below median, cross has occurred
        if mini_ratio[0] > series_median:
            if mini_ratio.min() <= series_median:
                mini_cross = 1
            else:
                mini_cross = 0
        
        period_cross_count = period_cross_count + mini_cross
    
    period_cross_frequency_perc = (period_cross_count / num_periods) * 100
    
    return period_cross_count, period_cross_frequency_perc
        

## Function for Building Crossing Results DF

In [24]:
def prob_crossing_again(ticker_df,
                        ticker1, ticker2,
                        train_start_date,train_end_date,
                        median_duration):

    ticker_df = ticker_df.reset_index()
    
    #create additional train start dates to look back further for checking long term medium & correlation levels
    train_start_date_2yr = train_start_date - timedelta(days = 365*2) 
    train_start_date_3yr = train_start_date - timedelta(days = 365*3) 
    train_start_date_5yr = train_start_date - timedelta(days = 365*5) 
    train_start_date_10yr = train_start_date - timedelta(days = 365*10) 
    
    #summary_array = np.empty((0, 16))
  
    #Create train df
    train_ticker_df = ticker_df[(ticker_df['Date'] > train_start_date) & (ticker_df['Date'] < train_end_date)]

    #Create Longer Term train dfs for checking long term medium & correlation levels
    train_ticker_df_2yr = ticker_df[(ticker_df['Date'] > train_start_date_2yr) & (ticker_df['Date'] < train_end_date)]
    train_ticker_df_3yr = ticker_df[(ticker_df['Date'] > train_start_date_3yr) & (ticker_df['Date'] < train_end_date)]
    train_ticker_df_5yr = ticker_df[(ticker_df['Date'] > train_start_date_5yr) & (ticker_df['Date'] < train_end_date)]
    train_ticker_df_10yr = ticker_df[(ticker_df['Date'] > train_start_date_10yr) & (ticker_df['Date'] < train_end_date)]

    train_ticker_df.set_index('Date', inplace=True)
    train_ticker_df_2yr.set_index('Date', inplace=True)
    train_ticker_df_3yr.set_index('Date', inplace=True)
    train_ticker_df_5yr.set_index('Date', inplace=True)
    train_ticker_df_10yr.set_index('Date', inplace=True)
       
    # create prices series
    train_series1, train_series2 = create_series(ticker1, ticker2, train_ticker_df, cross_market_settings)
    # create longer term price serieses for checking long term medium & correlation levels
    train_series1_2yr, train_series2_2yr = create_series(ticker1, ticker2, train_ticker_df_2yr, cross_market_settings)
    train_series1_3yr, train_series2_3yr = create_series(ticker1, ticker2, train_ticker_df_3yr, cross_market_settings)
    train_series1_5yr, train_series2_5yr = create_series(ticker1, ticker2, train_ticker_df_5yr, cross_market_settings)
    train_series1_10yr, train_series2_10yr = create_series(ticker1, ticker2, train_ticker_df_10yr, cross_market_settings)
        
    # Calculate Series Median
    series_median_1yr = np.median(train_series1/train_series2)

    #Calculate Longer Term Series Medians
    series_median_2yr = np.median(train_series1_2yr/train_series2_2yr)
    series_median_3yr = np.median(train_series1_3yr/train_series2_3yr)
    series_median_5yr = np.median(train_series1_5yr/train_series2_5yr)
    series_median_10yr = np.median(train_series1_10yr/train_series2_10yr)

    # Set the median to use based on median_duration variable
    if median_duration == 1:
        series_median = series_median_1yr
    if median_duration == 2:
        series_median = series_median_2yr
    if median_duration == 3:
        series_median = series_median_3yr
    if median_duration == 5:
        series_median = series_median_5yr
    if median_duration == 10:
        series_median = series_median_10yr
        
    #Calculate the size of the devn from the median
    current_ratio = train_series1[-1]/ train_series2[-1]
    devn_from_median = (current_ratio - series_median)/ series_median * 100
    # Calculate deviatin from long term median
    devn_from_5yr_median = (current_ratio - series_median_5yr)/ series_median_5yr * 100
    
    #### Calculate Cross Statistics for 'Training' Set ####
    train_series_df, train_median_count, train_first_cross, train_last_cross, series_median_train, train_days_last_cross = \
    median_cross_count(train_series1,train_series2, series_median)

    ### Calculate correlation across the multiple timeframes
    ###     Only use time series up to last crossing date for purposes of correlation calculation
    ##      Do this as that way the recent divergence does not impact on the correlation calc
    
    pair_corr_1yr = train_series1.corr(train_series2)
    pair_corr_2yr = train_series1_2yr.corr(train_series2_2yr)
    pair_corr_3yr = train_series1_3yr.corr(train_series2_3yr)
    pair_corr_5yr = train_series1_5yr.corr(train_series2_5yr)
    pair_corr_10yr = train_series1_10yr.corr(train_series2_10yr)
    
    # Calculate pvalue across multiple timeframes
    pscore_1yr, pvalue_1yr, _ = coint(train_series1,train_series2)
    pscore_2yr, pvalue_2yr, _ = coint(train_series1_2yr,train_series2_2yr)
    pscore_3yr, pvalue_3yr, _ = coint(train_series1_3yr,train_series2_3yr)
    pscore_5yr, pvalue_5yr, _ = coint(train_series1_5yr,train_series2_5yr)
    pscore_10yr, pvalue_10yr, _ = coint(train_series1_10yr,train_series2_10yr)

    #Calculate Regularity of Crosses
    period_cross_count, period_cross_frequency_perc = \
    regularity_of_crossing_func(train_series1_5yr, train_series2_5yr, series_median_5yr)
    
    # Build Results Array
    results_array = [[ticker1, ticker2, 
                            train_median_count, 
                            train_days_last_cross, 
                            current_ratio, 
                            series_median, devn_from_median, devn_from_5yr_median,
                            train_start_date, train_end_date,
                            pair_corr_1yr, pair_corr_2yr, pair_corr_3yr, pair_corr_5yr, pair_corr_10yr,
                            pvalue_1yr, pvalue_2yr, pvalue_3yr, pvalue_5yr, pvalue_10yr,
                            period_cross_count, period_cross_frequency_perc,
                            ]]
      
    results_df = pd.DataFrame(data=results_array, columns=['Ticker1', 'Ticker2', 'Train Median Cross Count',
                                   'Days Since Last TRAIN Cross', 
                                   'Current Ratio', 
                                   'Median Ratio', '% Deviation From Median', '% Deviation From 5Yr Median',
                                   'Train Start Date', 'Train End Date',
                                   '1 Yr Corr', '2 Yr Corr', '3 Yr Corr', '5 Yr Corr', '10 Yr Corr',
                                   '1 Yr P-Val', '2 Yr P-Val', '3 Yr P-Val', '5 Yr P-Val', '10 Yr P-Val',                                                            
                                    'Cross Freq Count', 'Cross Freq %'])

    return results_df


## Calculate Vol and Number of Std Devns

In [25]:
def pvalue_calc(series1,series2):
  score, pvalue, _ = coint(series1,series2)
  #print('CoInt score:', score, 'pvalue: ', pvalue)
  
  return score, pvalue

In [26]:
#Calculate the volatility of returns of the price series
# Vol period is the number of days to utilize to calculate the historical vol

def calculate_vol(series1, series2, vol_period, loss_limit):
  ratio = series1/ series2
  vol_period_ratio = ratio[-vol_period:]
  ratio_df = pd.DataFrame(data=vol_period_ratio, columns=['Ratio'])
  ratio_df['Ratio Return'] = ratio_df['Ratio'].pct_change() * 100
  ratio_df.dropna(inplace=True)
  daily_std_dev  = statistics.stdev(ratio_df['Ratio Return'])

  #annualize the standard dev
  vol = daily_std_dev * math.sqrt(252)  #annualized vol
  period_vol = daily_std_dev * math.sqrt(vol_period) #std devn for the period length chosen

  current_ratio = ratio[-1]
  median_ratio = ratio.median()
  devn_from_median = ((current_ratio - median_ratio) / median_ratio) * 100

  ##### Number of Standard Deviations and Z Score Probability ####
  #num_std_devs = (current_ratio - series_median) / vol #Calculating from Median Not Mean
  num_std_devs = devn_from_median / vol #Calculating from Median Not Mean
  prob_z_score = 100 - st.norm.cdf(abs(num_std_devs)) * 100

  #### Probability of Exceeding Set Loss %
  annual_stop_loss_sds = loss_limit / vol  #the number of standard deviations to reach the stop loss limit
  annual_prob_stop_loss = 100 - st.norm.cdf(abs(annual_stop_loss_sds)) * 100
  period_stop_loss_sds = loss_limit / period_vol  #the number of standard deviations to reach the stop loss limit
  period_prob_stop_loss = 100 - st.norm.cdf(abs(period_stop_loss_sds)) * 100

  #### Position Size Adjustment to Limit Dollar Loss to Target Stop Loss with 82% Confidence
  # 1 Std deviation = 68% Confidence = 1- 18% = 82% Confidence given only worried about one side of the curve
  annual_size_adjustment_multiple = loss_limit / vol
  period_size_adjustment_multiple = loss_limit / period_vol

  return vol, num_std_devs, prob_z_score, loss_limit, annual_prob_stop_loss, annual_size_adjustment_multiple, period_prob_stop_loss, period_size_adjustment_multiple

## Function to Plot Price Ratios vs Mean

In [27]:
##Plotting Price of One ticker divided by Price of Second Ticker vs the average of that
# Shows whether the ratio is mean reverting.
def plot_ratios_v_mean(series1, series2):

    start_date = str(series1.index[0].day) + "-" + str(series1.index[0].month)  + "-" + str(series1.index[0].year)  
    end_date = str(series1.index[-1].day) + "-" + str(series1.index[-1].month) + "-" + str(series1.index[-1].year)
    
    ratio = series1/series2

    medn = np.round((series1/series2).median(),2)
    minimum = np.round((series1/series2).min(),2)
    maximum = np.round((series1/series2).max(),2)
    current = np.round(series1[-1]/ series2[-1],2)
    
    trace1 = go.Scatter(x=list(series1.index),
                   y=list(ratio),
                   mode='lines',
                   text=ratio,
                   name='Price Ratio')

    trace2 = go.Scatter(x=list(series1.index),
                   y=list(ratio/ratio * medn),
                   mode='lines',
                   text=ratio,
                   name='Median Ratio')

    trace3 = go.Scatter(x=list(series1.index),
                   y=list(ratio/ratio * current),
                   mode='lines',
                   text=ratio,
                   name='Current Ratio')

    trace4 = go.Scatter(x=list(series1.index),
                   y=list(ratio/ratio * minimum),
                   mode='lines',
                   text=ratio,
                   name='Min Ratio')
    
    trace5 = go.Scatter(x=list(series1.index),
                   y=list(ratio/ratio * maximum),
                   mode='lines',
                   text=ratio,
                   name='Max Ratio') 
    
    data=[trace1, trace2, trace3, trace4, trace5]
    
    layout = go.Layout(title=series1.name + " vs " + series2.name + "   "  + start_date + " to " + end_date )

    figure = go.Figure(data=data, layout=layout)

    f1 = go.FigureWidget(figure)
    f1.show()
    

# Run Functions

In [28]:
ticker1 = ticker_list[0][0]
ticker2 = ticker_list[1][0]

In [29]:
#Use the Close, the Adj Close or the Open
#close_or_adj_close = 'Adj Close'
#close_or_adj_close = 'Open'
      
#if close_or_adj_close == 'Close':
#  price_to_use = 'USD Stock Close'
#if close_or_adj_close == 'Adj Close':
#  price_to_use = 'USD Stock Adj Close'
#if close_or_adj_close == 'Open':
#  price_to_use = 'USD Stock Open'

# Same Region
#prices_to_use = ['USD Stock Adj Close', 'USD Stock Adj Close']
#prices_to_use = ['USD Stock Close', 'USD Stock Close']

# Cross Region (EG US vs Australia: Use the Opening price for the US stock)
cross_market_settings = True



## Calculate Number of Crosses

In [30]:
last_train_date = datetime.today().date()
#last_train_date = '2019-12-31'
last_train_date = pd.to_datetime(last_train_date, format='%Y-%m-%d')
train_period_length = timedelta(days = 365)

# Training Period
train_start_date = last_train_date - timedelta(days = 365)
train_end_date = last_train_date

print('Training Period: ',train_start_date, 'to', train_end_date)

Training Period:  2022-03-17 00:00:00 to 2023-03-17 00:00:00


In [31]:
median_duration = 2 #Use the 1, 2, 5 or 10 year median to check deviations against and set as trading reversion point

#Run Prob of Crossing Again Function
results_df = prob_crossing_again(ticker_df,
                      ticker1, ticker2,
                      train_start_date, train_end_date,
                      median_duration)

results_df['Av Corr'] = (results_df['1 Yr Corr'] + results_df['2 Yr Corr'] + results_df['5 Yr Corr'] + 
                         results_df['10 Yr Corr'])  / 4

results_df['Median P-Val'] = results_df.loc[:,'1 Yr P-Val':'10 Yr P-Val'].median(axis=1)

results_df

Ticker1 Ticker2  Train Median Cross Count  Days Since Last TRAIN Cross  \
0     RIO  RIO.AX                        51                           13   

   Current Ratio  Median Ratio  % Deviation From Median  \
0       0.833082      0.893222                -6.733026   

   % Deviation From 5Yr Median Train Start Date Train End Date  ...  \
0                    -6.056681       2022-03-17     2023-03-17  ...   

   10 Yr Corr  1 Yr P-Val  2 Yr P-Val  3 Yr P-Val  5 Yr P-Val  10 Yr P-Val  \
0     0.97888    0.745598    0.287025    0.191588    0.291577     0.162603   

   Cross Freq Count  Cross Freq %   Av Corr  Median P-Val  
0                 5     83.333333  0.980025      0.287025  

[1 rows x 24 columns]

## Run Graphs

In [32]:
start_dates = ['2000-01-01', '2010-01-01','2015-01-01', '2019-01-01','2022-01-01', '2023-01-31']
end_date = '2030-01-01'
#end_date = '2018-04-01'

In [33]:
results_df.columns

Index(['Ticker1', 'Ticker2', 'Train Median Cross Count',
       'Days Since Last TRAIN Cross', 'Current Ratio', 'Median Ratio',
       '% Deviation From Median', '% Deviation From 5Yr Median',
       'Train Start Date', 'Train End Date', '1 Yr Corr', '2 Yr Corr',
       '3 Yr Corr', '5 Yr Corr', '10 Yr Corr', '1 Yr P-Val', '2 Yr P-Val',
       '3 Yr P-Val', '5 Yr P-Val', '10 Yr P-Val', 'Cross Freq Count',
       'Cross Freq %', 'Av Corr', 'Median P-Val'],
      dtype='object')

In [34]:
results_df[['Ticker1', 'Ticker2', 'Train Median Cross Count',
       'Days Since Last TRAIN Cross', 'Current Ratio', 'Median Ratio',
       '% Deviation From Median', '% Deviation From 5Yr Median',
       'Train Start Date', 'Train End Date', 
       'Cross Freq %', 'Av Corr', 'Median P-Val',
        #'1 Yr Corr', '2 Yr Corr','3 Yr Corr', '5 Yr Corr', '10 Yr Corr', 
        '1 Yr P-Val', '2 Yr P-Val','3 Yr P-Val', '5 Yr P-Val', '10 Yr P-Val', 
        'Cross Freq Count']]

Ticker1 Ticker2  Train Median Cross Count  Days Since Last TRAIN Cross  \
0     RIO  RIO.AX                        51                           13   

   Current Ratio  Median Ratio  % Deviation From Median  \
0       0.833082      0.893222                -6.733026   

   % Deviation From 5Yr Median Train Start Date Train End Date  Cross Freq %  \
0                    -6.056681       2022-03-17     2023-03-17     83.333333   

    Av Corr  Median P-Val  1 Yr P-Val  2 Yr P-Val  3 Yr P-Val  5 Yr P-Val  \
0  0.980025      0.287025    0.745598    0.287025    0.191588    0.291577   

   10 Yr P-Val  Cross Freq Count  
0     0.162603                 5

In [35]:
stock_prices_df.columns

Index(['Date', 'Open', 'Stock Close', 'Stock Adj Close', 'Ticker', 'Currency',
       'SGD', 'AUD', 'JPY', 'EUR', 'USD', 'HKD', 'Stock USD Close',
       'Stock USD Adj Close', 'Stock USD Open'],
      dtype='object')

In [37]:
for start_date in start_dates:

    indiv_df = stock_prices_df[stock_prices_df['Date'] > start_date].copy()
    indiv_df = indiv_df[indiv_df['Date'] < end_date].copy()
    indiv_df.set_index('Date', inplace=True)

    series1, series2 = create_series(ticker1, ticker2, indiv_df, cross_market_settings)

    plot_ratios_v_mean(series1, series2) 

    # print the pvalue & correlation
    score, pvalue = pvalue_calc(series1,series2)
    pair_corr = series1.corr(series2)
    print('pvalue: ', np.round(pvalue,4), 'Correlation: ', np.round(pair_corr,4))

    current_ratio = series1[-1]/ series2[-1]
    median_ratio = (series1/series2).median()
    diff = (current_ratio-median_ratio) / median_ratio * 100

    print('Median: ', np.round(median_ratio,3))
    print('Current Ratio: ', np.round(current_ratio,3))
    print('Current Diff Vs Median: ',  np.round(diff,2), '%')

    last_price_1 = stock_prices_df[stock_prices_df['Ticker']==ticker1]['Stock USD Adj Close'].values[-1].round(2)
    last_price_2a = stock_prices_df[stock_prices_df['Ticker']==ticker2]['Open'].values[-1].round(2)
    last_price_2b = stock_prices_df[stock_prices_df['Ticker']==ticker2]['Stock USD Open'].values[-1].round(2)
    
    print(f"Last prices used: {ticker1} {last_price_1} {ticker2} Local Ccy: {last_price_2a} USD: {last_price_2b}") 


    #print the vol and number of standard deviations divergence
    vol, num_std_devs, prob_z_score, loss_limit, annual_prob_stop_loss, annual_size_adjustment_multiple, \
    period_prob_stop_loss, period_size_adjustment_multiple = \
    calculate_vol(series1, series2, vol_period, loss_limit)

    print(vol_period, 'Day Historical Volality', np.round(vol,2),'%')
    print('Probability of stop loss (', loss_limit,'%) being exceeded within', vol_period,'days', np.round(period_prob_stop_loss,2),'%')
    print('Size Adjustment Multiple for 82% Confidence at Stop Loss Level of', loss_limit,'% =', np.round(period_size_adjustment_multiple,3))

results_df   #display crossing results

pvalue:  0.5132 Correlation:  0.907
Median:  0.888
Current Ratio:  0.833
Current Diff Vs Median:  -6.2 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


pvalue:  0.3218 Correlation:  0.9677
Median:  0.873
Current Ratio:  0.833
Current Diff Vs Median:  -4.58 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


pvalue:  0.2568 Correlation:  0.9875
Median:  0.89
Current Ratio:  0.833
Current Diff Vs Median:  -6.36 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


pvalue:  0.1703 Correlation:  0.9792
Median:  0.878
Current Ratio:  0.833
Current Diff Vs Median:  -5.12 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


pvalue:  0.1596 Correlation:  0.9714
Median:  0.899
Current Ratio:  0.833
Current Diff Vs Median:  -7.3 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


pvalue:  0.0 Correlation:  0.9253
Median:  0.865
Current Ratio:  0.833
Current Diff Vs Median:  -3.67 %
Last prices used: RIO 64.73 RIO.AX Local Ccy: 114.1 USD: 76.32
20 Day Historical Volality 42.11 %
Probability of stop loss ( 10 %) being exceeded within 20 days 19.96 %
Size Adjustment Multiple for 82% Confidence at Stop Loss Level of 10 % = 0.843


Ticker1 Ticker2  Train Median Cross Count  Days Since Last TRAIN Cross  \
0     RIO  RIO.AX                        51                           13   

   Current Ratio  Median Ratio  % Deviation From Median  \
0       0.833082      0.893222                -6.733026   

   % Deviation From 5Yr Median Train Start Date Train End Date  ...  \
0                    -6.056681       2022-03-17     2023-03-17  ...   

   10 Yr Corr  1 Yr P-Val  2 Yr P-Val  3 Yr P-Val  5 Yr P-Val  10 Yr P-Val  \
0     0.97888    0.745598    0.287025    0.191588    0.291577     0.162603   

   Cross Freq Count  Cross Freq %   Av Corr  Median P-Val  
0                 5     83.333333  0.980025      0.287025  

[1 rows x 24 columns]

# SIZE OF TRADE

In [ ]:
series1[-1]


In [ ]:
series2[-1]

In [ ]:
#Input Desired Position Dollar Size
pair_size = 5000

In [ ]:
#Set Direction
if results_df.loc[0,'% Deviation From Median'] < 0:
    ticker1_direction = 'BUY'
    ticker2_direction = 'SELL'
else:
    ticker1_direction = 'SELL'
    ticker2_direction = 'BUY'   
    

In [ ]:
ticker1_price = series1[-1]
ticker2_price = series2[-1]

ticker1_qty = pair_size /ticker1_price
ticker2_qty = pair_size /ticker2_price

print(ticker1_direction, int(np.round(ticker1_qty,0)), 'shares of', ticker1 )
print(ticker2_direction, int(np.round(ticker2_qty,0)), 'shares of', ticker2 )
